In [4]:
import os
import re
import requests
from urllib.parse import urlencode#
from dotenv import load_dotenv

load_dotenv()

# Configure session to handle cookies
session = requests.Session()

# Environment variables for credentials (assumed to be set in your environment)
EZPROXY_USER = os.getenv("EZPROXY_USER")
EZPROXY_PASS = os.getenv("EZPROXY_PASS")

# URL and parameters setup
ezproxy_url_prefix = "https://login.ezproxy.lhlt.mpg.de/login?qurl="
params = {
    "user": EZPROXY_USER,
    "pass": EZPROXY_PASS,
    "login": "Login"
}

params_encoded = urlencode(params)

def download_via_ezproxy(url, file_path):
    # Login with credentials and fetch content
    res = session.post(ezproxy_url_prefix + url, data=params_encoded)
    res = session.get(res.url)  # Follow redirect
    content_type = res.headers["Content-Type"].split(";")[0]
    size = 0
    
    if content_type == "text/html":
        # Check for access restrictions or find the real document URL
        html = res.text
        
        if "You currently have no access" in html:
            raise Exception("No access")

        match = re.search(r'click \<a href="([^"]+)"', html)
        if match:
            url = match.group(1)
        else:
            with open("out/invalid-response.html", "w", encoding="utf-8") as f:
                f.write(html)
            raise Exception("Invalid html response")

        # Refetch from the new URL
        print(url)
        res = session.get(url)
        print(res.headers)
        content_type = res.headers["Content-Type"].split(";")[0]

    if content_type == "application/pdf":
        # Download PDF document
        with open(file_path, "wb") as f:
            for chunk in res.iter_content(chunk_size=8192):
                size += len(chunk)
                f.write(chunk)
    else:
        raise Exception(f"Unexpected response of type {content_type}")

    return size

download_via_ezproxy("https://www.jstor.org/stable/pdf/20805575.pdf", "out/20805575.pdf")


https://www-jstor-org.ezproxy.lhlt.mpg.de/stable/pdf/20805575.pdf
{'Server': 'Varnish', 'Retry-After': '0', 'Content-Type': '', 'Date': 'Fri, 22 Mar 2024 21:42:32 GMT', 'Via': '1.1 varnish', 'X-Served-By': 'cache-fra-eddf8230065-FRA', 'X-Cache': 'MISS', 'X-Cache-Hits': '0', 'Accept-Ranges': 'none', 'Connection': 'close'}


Exception: Unexpected response of type 